## Limpeza de dados Cartola ano 2014

In [1]:
from pyspark.sql import HiveContext
from pyspark.sql.types import IntegerType
from pyspark.sql.functions import lower, col, lit, regexp_replace
import pandas as pd
import json
import requests

## Times

In [2]:
times_2014_df = spark.read.csv("/cartola/data/2014/2014_times.csv", header=True)
sorted_times_2014_df = times_2014_df.sort(times_2014_df.ID.desc())

#Chegar se o arquivo está no hdfs

times_2014_ano = times_2014_df.withColumn('ano', lit(2014))
times_2014_ano.show()
#times_2014_ano.write.partitionBy('ano').parquet('/cartola/clean/times')


+---+-------------+----------+-------------+----+
| ID|         Nome|Abreviacao|         Slug| ano|
+---+-------------+----------+-------------+----+
|262|     flamengo|       FLA|     flamengo|2014|
|263|     botafogo|       BOT|     botafogo|2014|
|264|  corinthians|       COR|  corinthians|2014|
|265|        bahia|       BAH|        bahia|2014|
|266|   fluminense|       FLU|   fluminense|2014|
|275|    palmeiras|       PAL|    palmeiras|2014|
|276|    são paulo|       SAO|    sao-paulo|2014|
|277|       santos|       SAN|       santos|2014|
|282|  atlético-mg|       CAM|  atletico-mg|2014|
|283|     cruzeiro|       CRU|     cruzeiro|2014|
|284|       grêmio|       GRE|       gremio|2014|
|285|internacional|       INT|internacional|2014|
|287|      vitória|       VIT|      vitoria|2014|
|288|     criciúma|       CRI|     criciuma|2014|
|290|        goiás|       GOI|        goias|2014|
|292|        sport|       SPO|        sport|2014|
|293|  atlético-pr|       CAP|  atletico-pr|2014|


In [3]:
times_2014_parquet = spark.read.parquet("/cartola/clean/times")

In [4]:
times_2014_parquet.show()
times_2014_parquet.schema

#Alterar ID para int.(está string)

+---+-------------+----------+-------------+----+
| ID|         Nome|Abreviacao|         Slug| ano|
+---+-------------+----------+-------------+----+
|262|     flamengo|       FLA|     flamengo|2014|
|263|     botafogo|       BOT|     botafogo|2014|
|264|  corinthians|       COR|  corinthians|2014|
|265|        bahia|       BAH|        bahia|2014|
|266|   fluminense|       FLU|   fluminense|2014|
|275|    palmeiras|       PAL|    palmeiras|2014|
|276|    são paulo|       SAO|    sao-paulo|2014|
|277|       santos|       SAN|       santos|2014|
|282|  atlético-mg|       CAM|  atletico-mg|2014|
|283|     cruzeiro|       CRU|     cruzeiro|2014|
|284|       grêmio|       GRE|       gremio|2014|
|285|internacional|       INT|internacional|2014|
|287|      vitória|       VIT|      vitoria|2014|
|288|     criciúma|       CRI|     criciuma|2014|
|290|        goiás|       GOI|        goias|2014|
|292|        sport|       SPO|        sport|2014|
|293|  atlético-pr|       CAP|  atletico-pr|2014|


StructType(List(StructField(ID,StringType,true),StructField(Nome,StringType,true),StructField(Abreviacao,StringType,true),StructField(Slug,StringType,true),StructField(ano,IntegerType,true)))

In [5]:
times_2014_parquet = times_2014_parquet.withColumn("ID", times_2014_parquet["ID"].cast(IntegerType()))

In [7]:
times_2014_parquet.schema

StructType(List(StructField(ID,IntegerType,true),StructField(Nome,StringType,true),StructField(Abreviacao,StringType,true),StructField(Slug,StringType,true),StructField(ano,IntegerType,true)))

In [8]:
sorted_times_2014_df.show()

print(sorted_times_2014_df.count())

+---+-------------+----------+-------------+
| ID|         Nome|Abreviacao|         Slug|
+---+-------------+----------+-------------+
|316|  figueirense|       FIG|  figueirense|
|315|  chapecoense|       CHA|  chapecoense|
|294|     coritiba|       CFC|     coritiba|
|293|  atlético-pr|       CAP|  atletico-pr|
|292|        sport|       SPO|        sport|
|290|        goiás|       GOI|        goias|
|288|     criciúma|       CRI|     criciuma|
|287|      vitória|       VIT|      vitoria|
|285|internacional|       INT|internacional|
|284|       grêmio|       GRE|       gremio|
|283|     cruzeiro|       CRU|     cruzeiro|
|282|  atlético-mg|       CAM|  atletico-mg|
|277|       santos|       SAN|       santos|
|276|    são paulo|       SAO|    sao-paulo|
|275|    palmeiras|       PAL|    palmeiras|
|266|   fluminense|       FLU|   fluminense|
|265|        bahia|       BAH|        bahia|
|264|  corinthians|       COR|  corinthians|
|263|     botafogo|       BOT|     botafogo|
|262|     

## Jogadores

In [9]:
#Carrega arquivo CSV
jogadores_2014_df = spark.read.csv("/cartola/data/2014/2014_jogadores.csv", header=True)
sorted_jogadores_2014_df = jogadores_2014_df.sort(jogadores_2014_df.ID.desc())


In [11]:
#Adiciona coluna ANO = 2014
jogadores_2014_ano = sorted_jogadores_2014_df.withColumn('ano', lit(2014))
jogadores_2014_ano.show()

+-----+-----------------+-------+---------+----+
|   ID|          Apelido|ClubeID|PosicaoID| ano|
+-----+-----------------+-------+---------+----+
|89977|     Bruno Santos|    316|        2|2014|
|89975|          Rodolfo|    282|        1|2014|
|89932|            JacÃ³|    265|        5|2014|
|89924|            Bruno|    283|        4|2014|
|89921|           Maikon|    263|        5|2014|
|89914|         Gabriel |    288|        4|2014|
|89898|            Roger|    288|        5|2014|
|89897|          Ronaldo|    288|        1|2014|
|89896|          Cleiton|    288|        2|2014|
|89885|          Leandro|    263|        4|2014|
|89884|            Kalil|    288|        5|2014|
|89883|             Dodi|    288|        4|2014|
|89815|Gustavo Ferrareis|    285|        4|2014|
|89694|       James Dean|    292|        5|2014|
|89681|    Mateus Muller|    275|        2|2014|
|89677|      Fernandinho|    275|        4|2014|
|89676|          Nickson|    287|        4|2014|
|89637|      Thiago 

In [12]:
jogadores_2014_ano.write.partitionBy('ano').parquet('/cartola/clean/jogadores')

AnalysisException: 'path hdfs://namenode:8020/cartola/clean/jogadores already exists.;'

In [13]:
#transforma arquivo em parquet
jogadores_2014_parquet = spark.read.parquet('/cartola/clean/jogadores')

In [14]:
jogadores_2014_parquet.show()
jogadores_2014_parquet.schema


+-----+-----------------+-------+---------+----+
|   ID|          Apelido|ClubeID|PosicaoID| ano|
+-----+-----------------+-------+---------+----+
|83511|     Érico Júnior|    292|        5|2014|
|83506|    Vítor Michels|    288|        4|2014|
|83471|         Paulinho|    264|        5|2014|
|83439|           Maykon|    294|        5|2014|
|83266|Marcos Guilherme |    293|        4|2014|
|83258|     Filipe Ramon|    294|        2|2014|
|51781|            Ávine|    265|        2|2014|
|51779|    Pedro Botelho|    282|        2|2014|
|51772|  Éverton Ribeiro|    283|        4|2014|
|51705|    Bruno Rodrigo|    283|        3|2014|
|51683|     Bruno Rangel|    315|        5|2014|
|51681|           Hélder|    294|        4|2014|
|69088|        Victorino|    275|        3|2014|
|69051| Danilo Fernandes|    264|        1|2014|
|69049|    Leandro Amaro|    315|        3|2014|
|69048|           Mazola|    316|        5|2014|
|69047|    Paulo Roberto|    316|        4|2014|
|69041|           Mu

StructType(List(StructField(ID,StringType,true),StructField(Apelido,StringType,true),StructField(ClubeID,StringType,true),StructField(PosicaoID,StringType,true),StructField(ano,IntegerType,true)))

In [15]:
#Alterar ID para int.(está string)
jogadores_2014_parquet = jogadores_2014_parquet.withColumn("ID", jogadores_2014_parquet["ID"].cast(IntegerType()))
jogadores_2014_parquet = jogadores_2014_parquet.withColumn("ClubeID", jogadores_2014_parquet["ClubeID"].cast(IntegerType()))
jogadores_2014_parquet = jogadores_2014_parquet.withColumn("PosicaoID", jogadores_2014_parquet["PosicaoID"].cast(IntegerType()))

In [16]:
jogadores_2014_parquet.schema

StructType(List(StructField(ID,IntegerType,true),StructField(Apelido,StringType,true),StructField(ClubeID,IntegerType,true),StructField(PosicaoID,IntegerType,true),StructField(ano,IntegerType,true)))

In [17]:
jogadores_2014_parquet.show()

print(jogadores_2014_parquet.count())

+-----+-----------------+-------+---------+----+
|   ID|          Apelido|ClubeID|PosicaoID| ano|
+-----+-----------------+-------+---------+----+
|83511|     Érico Júnior|    292|        5|2014|
|83506|    Vítor Michels|    288|        4|2014|
|83471|         Paulinho|    264|        5|2014|
|83439|           Maykon|    294|        5|2014|
|83266|Marcos Guilherme |    293|        4|2014|
|83258|     Filipe Ramon|    294|        2|2014|
|51781|            Ávine|    265|        2|2014|
|51779|    Pedro Botelho|    282|        2|2014|
|51772|  Éverton Ribeiro|    283|        4|2014|
|51705|    Bruno Rodrigo|    283|        3|2014|
|51683|     Bruno Rangel|    315|        5|2014|
|51681|           Hélder|    294|        4|2014|
|69088|        Victorino|    275|        3|2014|
|69051| Danilo Fernandes|    264|        1|2014|
|69049|    Leandro Amaro|    315|        3|2014|
|69048|           Mazola|    316|        5|2014|
|69047|    Paulo Roberto|    316|        4|2014|
|69041|           Mu

## Partidas_IDS

In [18]:
partidas_ids_2014_df = spark.read.csv("/cartola/data/2014/2014_partidas_ids.csv", header=True)

In [19]:
partidas_ids_2014_ano = partidas_ids_2014_df.withColumn('ano', lit(2014))

In [20]:
partidas_ids_2014_ano.show(1000)

+------+------+----+---------+----------+---------------+---------+----+
|    ID|Rodada|Casa|Visitante|PlacarCasa|PlacarVisitante|Resultado| ano|
+------+------+----+---------+----------+---------------+---------+----+
|179872|     1| 262|      290|         0|              0|   Empate|2014|
|179873|     1| 266|      316|         3|              0|     Casa|2014|
|179874|     1| 276|      263|         3|              0|     Casa|2014|
|179875|     1| 277|      292|         1|              1|   Empate|2014|
|179876|     1| 293|      284|         1|              0|     Casa|2014|
|179877|     1| 282|      264|         0|              0|   Empate|2014|
|179878|     1| 265|      283|         1|              2|Visitante|2014|
|179879|     1| 285|      287|         1|              0|     Casa|2014|
|179880|     1| 288|      275|         1|              2|Visitante|2014|
|179881|     1| 315|      294|         0|              0|   Empate|2014|
|179882|     2| 263|      285|         2|          

In [ ]:
partidas_ids_2014_ano.write.partitionBy('ano').parquet('/cartola/clean/partidas_ids')

In [21]:
partidas_ids_2014_parquet = spark.read.parquet('/cartola/clean/partidas_ids')

In [22]:
partidas_ids_2014_parquet.show(10000)
partidas_ids_2014_parquet.schema

+------+------+----+---------+----------+---------------+---------+----+
|    ID|Rodada|Casa|Visitante|PlacarCasa|PlacarVisitante|Resultado| ano|
+------+------+----+---------+----------+---------------+---------+----+
|179872|     1| 262|      290|         0|              0|   Empate|2014|
|179873|     1| 266|      316|         3|              0|     Casa|2014|
|179874|     1| 276|      263|         3|              0|     Casa|2014|
|179875|     1| 277|      292|         1|              1|   Empate|2014|
|179876|     1| 293|      284|         1|              0|     Casa|2014|
|179877|     1| 282|      264|         0|              0|   Empate|2014|
|179878|     1| 265|      283|         1|              2|Visitante|2014|
|179879|     1| 285|      287|         1|              0|     Casa|2014|
|179880|     1| 288|      275|         1|              2|Visitante|2014|
|179881|     1| 315|      294|         0|              0|   Empate|2014|
|179882|     2| 263|      285|         2|          

StructType(List(StructField(ID,StringType,true),StructField(Rodada,StringType,true),StructField(Casa,StringType,true),StructField(Visitante,StringType,true),StructField(PlacarCasa,StringType,true),StructField(PlacarVisitante,StringType,true),StructField(Resultado,StringType,true),StructField(ano,IntegerType,true)))

In [23]:
partidas_ids_2014_parquet = partidas_ids_2014_parquet.withColumn("ID", partidas_ids_2014_parquet["ID"].cast(IntegerType()))
partidas_ids_2014_parquet = partidas_ids_2014_parquet.withColumn("Rodada", partidas_ids_2014_parquet["Rodada"].cast(IntegerType()))
partidas_ids_2014_parquet = partidas_ids_2014_parquet.withColumn("Casa", partidas_ids_2014_parquet["Casa"].cast(IntegerType()))
partidas_ids_2014_parquet = partidas_ids_2014_parquet.withColumn("Visitante", partidas_ids_2014_parquet["Visitante"].cast(IntegerType()))
partidas_ids_2014_parquet = partidas_ids_2014_parquet.withColumn("PlacarCasa", partidas_ids_2014_parquet["PlacarVisitante"].cast(IntegerType()))
partidas_ids_2014_parquet = partidas_ids_2014_parquet.withColumn("PlacarVisitante", partidas_ids_2014_parquet["PlacarVisitante"].cast(IntegerType()))

In [24]:
partidas_ids_2014_parquet.show()

print(partidas_ids_2014_parquet.count())

+------+------+----+---------+----------+---------------+---------+----+
|    ID|Rodada|Casa|Visitante|PlacarCasa|PlacarVisitante|Resultado| ano|
+------+------+----+---------+----------+---------------+---------+----+
|179872|     1| 262|      290|         0|              0|   Empate|2014|
|179873|     1| 266|      316|         0|              0|     Casa|2014|
|179874|     1| 276|      263|         0|              0|     Casa|2014|
|179875|     1| 277|      292|         1|              1|   Empate|2014|
|179876|     1| 293|      284|         0|              0|     Casa|2014|
|179877|     1| 282|      264|         0|              0|   Empate|2014|
|179878|     1| 265|      283|         2|              2|Visitante|2014|
|179879|     1| 285|      287|         0|              0|     Casa|2014|
|179880|     1| 288|      275|         2|              2|Visitante|2014|
|179881|     1| 315|      294|         0|              0|   Empate|2014|
|179882|     2| 263|      285|         2|          

## LANCES (Criar a tabela de scouts a partir da tabela lances)

In [25]:
lances_2014_df = spark.read.csv("/cartola/data/2014/2014_lances.csv", header=True)

In [26]:
lances_2014_ano = lances_2014_df.withColumn('ano', lit(2014))

In [28]:
lances_2014_ano.show(1000)

+---------+---------+-------+--------+-------+-------+----+----+
|       ID|PartidaID|ClubeID|AtletaID|Periodo|Momento|Tipo| ano|
+---------+---------+-------+--------+-------+-------+----+----+
|121677889|   180064|    263|   38523|    1tr|      3|  FC|2014|
|121677887|   180064|    263|   37621|    1tr|      2|  FR|2014|
|121677886|   180064|    263|   37621|    1tr|      2|  RB|2014|
|121677884|   180064|    263|   38523|    1tr|      2|  FC|2014|
|121677882|   180064|    263|   37789|    1tr|      1|  PE|2014|
|121677880|   180064|    263|   73540|    1tr|      1|  FR|2014|
|121737581|   180064|    263|   38523|    1tr|     25|  ZG|2014|
|121737585|   180064|    263|   38523|    1tr|     14|  CA|2014|
|121737584|   180064|    263|   68744|    2tr|      3|  CA|2014|
|121677930|   180064|    263|   69232|    1tr|     21|  FC|2014|
|121677936|   180064|    263|   37652|    1tr|     23|  IM|2014|
|121677935|   180064|    263|   38523|    1tr|     23|  ZD|2014|
|121677939|   180064|    

In [29]:
lances_2014_ano.write.partitionBy('ano').parquet('/cartola/clean/lances')

AnalysisException: 'path hdfs://namenode:8020/cartola/clean/lances already exists.;'

In [30]:
lances_2014_parquet = spark.read.parquet('/cartola/clean/lances')

In [31]:
lances_2014_parquet.show(10000)
lances_2014_parquet.schema

+---------+---------+-------+--------+-------+-------+----+----+
|       ID|PartidaID|ClubeID|AtletaID|Periodo|Momento|Tipo| ano|
+---------+---------+-------+--------+-------+-------+----+----+
|121677889|   180064|    263|   38523|    1tr|      3|  FC|2014|
|121677887|   180064|    263|   37621|    1tr|      2|  FR|2014|
|121677886|   180064|    263|   37621|    1tr|      2|  RB|2014|
|121677884|   180064|    263|   38523|    1tr|      2|  FC|2014|
|121677882|   180064|    263|   37789|    1tr|      1|  PE|2014|
|121677880|   180064|    263|   73540|    1tr|      1|  FR|2014|
|121737581|   180064|    263|   38523|    1tr|     25|  ZG|2014|
|121737585|   180064|    263|   38523|    1tr|     14|  CA|2014|
|121737584|   180064|    263|   68744|    2tr|      3|  CA|2014|
|121677930|   180064|    263|   69232|    1tr|     21|  FC|2014|
|121677936|   180064|    263|   37652|    1tr|     23|  IM|2014|
|121677935|   180064|    263|   38523|    1tr|     23|  ZD|2014|
|121677939|   180064|    

StructType(List(StructField(ID,StringType,true),StructField(PartidaID,StringType,true),StructField(ClubeID,StringType,true),StructField(AtletaID,StringType,true),StructField(Periodo,StringType,true),StructField(Momento,StringType,true),StructField(Tipo,StringType,true),StructField(ano,IntegerType,true)))

In [32]:
lances_2014_parquet = lances_2014_parquet.withColumn("ID", lances_2014_parquet["ID"].cast(IntegerType()))
lances_2014_parquet = lances_2014_parquet.withColumn("PartidaID", lances_2014_parquet["PartidaID"].cast(IntegerType()))
lances_2014_parquet = lances_2014_parquet.withColumn("ClubeID", lances_2014_parquet["ClubeID"].cast(IntegerType()))
lances_2014_parquet = lances_2014_parquet.withColumn("AtletaID", lances_2014_parquet["AtletaID"].cast(IntegerType()))
lances_2014_parquet = lances_2014_parquet.withColumn("Momento", lances_2014_parquet["Momento"].cast(IntegerType()))

In [33]:
lances_2014_parquet.show()

print(lances_2014_parquet.count())

+---------+---------+-------+--------+-------+-------+----+----+
|       ID|PartidaID|ClubeID|AtletaID|Periodo|Momento|Tipo| ano|
+---------+---------+-------+--------+-------+-------+----+----+
|121677889|   180064|    263|   38523|    1tr|      3|  FC|2014|
|121677887|   180064|    263|   37621|    1tr|      2|  FR|2014|
|121677886|   180064|    263|   37621|    1tr|      2|  RB|2014|
|121677884|   180064|    263|   38523|    1tr|      2|  FC|2014|
|121677882|   180064|    263|   37789|    1tr|      1|  PE|2014|
|121677880|   180064|    263|   73540|    1tr|      1|  FR|2014|
|121737581|   180064|    263|   38523|    1tr|     25|  ZG|2014|
|121737585|   180064|    263|   38523|    1tr|     14|  CA|2014|
|121737584|   180064|    263|   68744|    2tr|      3|  CA|2014|
|121677930|   180064|    263|   69232|    1tr|     21|  FC|2014|
|121677936|   180064|    263|   37652|    1tr|     23|  IM|2014|
|121677935|   180064|    263|   38523|    1tr|     23|  ZD|2014|
|121677939|   180064|    

## scouts_raw

In [34]:
scouts_raw_2014_df = spark.read.csv("/cartola/data/2014/2014_scouts_raw.csv", header=True)

In [35]:
scouts_raw_2014_ano = scouts_raw_2014_df.withColumn('ano', lit(2014))

In [36]:
scouts_raw_2014_ano.show(1000)

+------+------+-----+----------+-------+-----+------+-----------+-----+-------------+-------+-----+-------+-----------+-------------------+----+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+----+
|Atleta|Rodada|Clube|Participou|Posicao|Jogos|Pontos|PontosMedia|Preco|PrecoVariacao|Partida|Mando|Titular|Substituido|        TempoJogado|Nota| FS| PE|  A| FT| FD| FF|  G|  I| PP| RB| FC| GC| CA| CV| SG| DD| DP| GS| ano|
+------+------+-----+----------+-------+-----+------+-----------+-----+-------------+-------+-----+-------+-----------+-------------------+----+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+----+
| 36443|     0| null|         0|   null|    0|     0|          0|    9|            0|   null|    0|   null|          0|               null|null|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|2014|
| 36443|     1|  285|         1|      1|    1|     5|          5| 10.6|          1.6| 179879|    1|      1|     

In [37]:
# remove todas as linhas com rodada == 0
scouts_raw_2014_ano_clean = scouts_raw_2014_ano[scouts_raw_2014_ano['Rodada'] > 0]

In [38]:
# remove todos os jogadores que não participaram de alguma rodada
scouts_raw_2014_ano_clean = scouts_raw_2014_ano_clean[(scouts_raw_2014_ano_clean['Participou'] == True) | (scouts_raw_2014_ano_clean['PrecoVariacao'] != 0)]

In [39]:
scouts_raw_2014_ano_clean.show(10000)

+------+------+-----+----------+-------+-----+------+-----------+-----+-------------+-------+-----+-------+-----------+-------------------+----+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+----+
|Atleta|Rodada|Clube|Participou|Posicao|Jogos|Pontos|PontosMedia|Preco|PrecoVariacao|Partida|Mando|Titular|Substituido|        TempoJogado|Nota| FS| PE|  A| FT| FD| FF|  G|  I| PP| RB| FC| GC| CA| CV| SG| DD| DP| GS| ano|
+------+------+-----+----------+-------+-----+------+-----------+-----+-------------+-------+-----+-------+-----------+-------------------+----+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+----+
| 36443|     1|  285|         1|      1|    1|     5|          5| 10.6|          1.6| 179879|    1|      1|          0|                  1|   6|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  1|  0|  0|  0|2014|
| 36443|     2|  285|         1|      1|    2|    -3|          1| 8.27|        -2.33| 179882|    0|      1|     

In [ ]:
scouts_raw_2014_ano_clean.write.partitionBy('ano').parquet('/cartola/clean/scouts_raw_2014')

In [40]:
scouts_raw_2014_parquet = spark.read.parquet('/cartola/clean/scouts_raw_2014')

In [41]:
scouts_raw_2014_parquet.show(10000)
scouts_raw_2014_parquet.schema

+------+------+-----+----------+-------+-----+------+-----------+-----+-------------+-------+-----+-------+-----------+-------------------+----+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+----+
|Atleta|Rodada|Clube|Participou|Posicao|Jogos|Pontos|PontosMedia|Preco|PrecoVariacao|Partida|Mando|Titular|Substituido|        TempoJogado|Nota| FS| PE|  A| FT| FD| FF|  G|  I| PP| RB| FC| GC| CA| CV| SG| DD| DP| GS| ano|
+------+------+-----+----------+-------+-----+------+-----------+-----+-------------+-------+-----+-------+-----------+-------------------+----+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+----+
| 36443|     1|  285|         1|      1|    1|     5|          5| 10.6|          1.6| 179879|    1|      1|          0|                  1|   6|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  1|  0|  0|  0|2014|
| 36443|     2|  285|         1|      1|    2|    -3|          1| 8.27|        -2.33| 179882|    0|      1|     

StructType(List(StructField(Atleta,StringType,true),StructField(Rodada,StringType,true),StructField(Clube,StringType,true),StructField(Participou,StringType,true),StructField(Posicao,StringType,true),StructField(Jogos,StringType,true),StructField(Pontos,StringType,true),StructField(PontosMedia,StringType,true),StructField(Preco,StringType,true),StructField(PrecoVariacao,StringType,true),StructField(Partida,StringType,true),StructField(Mando,StringType,true),StructField(Titular,StringType,true),StructField(Substituido,StringType,true),StructField(TempoJogado,StringType,true),StructField(Nota,StringType,true),StructField(FS,StringType,true),StructField(PE,StringType,true),StructField(A,StringType,true),StructField(FT,StringType,true),StructField(FD,StringType,true),StructField(FF,StringType,true),StructField(G,StringType,true),StructField(I,StringType,true),StructField(PP,StringType,true),StructField(RB,StringType,true),StructField(FC,StringType,true),StructField(GC,StringType,true),Stru

In [42]:
#deve-se converter valores em BigDecimal?
scouts_raw_2014_parquet = scouts_raw_2014_parquet.withColumn("Atleta", scouts_raw_2014_parquet["Atleta"].cast(IntegerType()))
scouts_raw_2014_parquet = scouts_raw_2014_parquet.withColumn("Rodada", scouts_raw_2014_parquet["Rodada"].cast(IntegerType()))
scouts_raw_2014_parquet = scouts_raw_2014_parquet.withColumn("Clube", scouts_raw_2014_parquet["Clube"].cast(IntegerType()))
scouts_raw_2014_parquet = scouts_raw_2014_parquet.withColumn("Participou", scouts_raw_2014_parquet["Participou"].cast(IntegerType()))
scouts_raw_2014_parquet = scouts_raw_2014_parquet.withColumn("Posicao", scouts_raw_2014_parquet["Posicao"].cast(IntegerType()))
scouts_raw_2014_parquet = scouts_raw_2014_parquet.withColumn("Jogos", scouts_raw_2014_parquet["Jogos"].cast(IntegerType()))
scouts_raw_2014_parquet = scouts_raw_2014_parquet.withColumn("Partida", scouts_raw_2014_parquet["Partida"].cast(IntegerType()))
scouts_raw_2014_parquet = scouts_raw_2014_parquet.withColumn("Mando", scouts_raw_2014_parquet["Mando"].cast(IntegerType()))
scouts_raw_2014_parquet = scouts_raw_2014_parquet.withColumn("Titular", scouts_raw_2014_parquet["Titular"].cast(IntegerType()))
scouts_raw_2014_parquet = scouts_raw_2014_parquet.withColumn("Participou", scouts_raw_2014_parquet["Participou"].cast(IntegerType()))

In [43]:
scouts_raw_2014_parquet.show()

print(scouts_raw_2014_parquet.count())

+------+------+-----+----------+-------+-----+------+-----------+-----+-------------+-------+-----+-------+-----------+-----------+----+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+----+
|Atleta|Rodada|Clube|Participou|Posicao|Jogos|Pontos|PontosMedia|Preco|PrecoVariacao|Partida|Mando|Titular|Substituido|TempoJogado|Nota| FS| PE|  A| FT| FD| FF|  G|  I| PP| RB| FC| GC| CA| CV| SG| DD| DP| GS| ano|
+------+------+-----+----------+-------+-----+------+-----------+-----+-------------+-------+-----+-------+-----------+-----------+----+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+----+
| 36443|     1|  285|         1|      1|    1|     5|          5| 10.6|          1.6| 179879|    1|      1|          0|          1|   6|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  0|  1|  0|  0|  0|2014|
| 36443|     2|  285|         1|      1|    2|    -3|          1| 8.27|        -2.33| 179882|    0|      1|          0|          1|   5|  2|  0|

## DEMONSTRAÇÃO

In [ ]:
partidas_2014_df = spark.read.csv("/cartola/data/2014/2014_jogadores.csv", header=True)
partidas_2014_ct = partidas_2014_df.withColumn('time', regexp_replace('home_team', ' - RJ', ''))
final_partidas = partidas_2014_ct.withColumn('time_low', lower(col('time'))).show(truncate=False)

In [ ]:
with_ano_partidas = partidas_2014_ct.withColumn('ano', lit(2014)).show(truncate=False)
with_ano_partidas.show()

In [ ]:
Comando para sobrescrever arquivo caso já existente.
Agrupar scouts por ID e contar (caso tenha duplicidade)